# Network Generation

In this notebook we build the network that is at the base of our model. 
- We start from data about Milan underground ([routes](https://dati.comune.milano.it/dataset/ds539_atm-percorsi-linee-metropolitane), [stops](https://dati.comune.milano.it/dataset/ds535_atm-fermate-linee-metropolitane), [sequence](https://dati.comune.milano.it/dataset/ds533_atm-composizione-percorsi-linee-metropolitane), and [orari](https://dati.comune.milano.it/dataset/ds537_atm-orari-linee-metropolitane)) and Milan surface transit ([routes](https://dati.comune.milano.it/dataset/ds538_atm-percorsi-linee-di-superficie-urbane), [stops](https://dati.comune.milano.it/dataset/ds534-atm-fermate-linee-di-superficie-urbane), [sequence](https://dati.comune.milano.it/dataset/ds532-atm-composizione-percorsi-linee-di-superficie-urbane), and [orari](https://dati.comune.milano.it/dataset/ds536_atm-orari-linee-di-superficie-urbane)) in order to extract the nodes, the edges of the graph and their attributes.
- We also retrieve the information from the dataframe on stops and amenities created in notebook 0 and use it as attribute for the nodes.
- Lastly, we create a dictionary containing information on the minute-by-minute timetables of all edges. This is done starting from data retrieved [here](https://transitfeeds.com/p/agenzia-mobilita-ambiente-territorio/341/latest).

# Table of Contents
1. [Libraries and Import data](#data)<br>
2. [DataFrame Manipulation](#df)<br>
3. [Creating the Network](#net)<br>
4. [Getting Routes Timetables](#route)<br>
5. [Saving Files](#save)<br>

In [1]:
# auxiliary function to print dataframes side by side
from IPython.display import display_html
from itertools import chain,cycle
def display_side_by_side(*args,titles=cycle([''])):
    html_str=''
    for df,title in zip(args, chain(titles,cycle(['</br>'])) ):
        html_str+='<th style="text-align:center"><td style="vertical-align:top">'
        html_str+=f'<h2>{title}</h2>'
        html_str+=df.to_html().replace('table','table style="display:inline"')
        html_str+='</td></th>'
    display_html(html_str,raw=True)

# 1. Libraries and Import Data <a name="data"></a>

In [1]:
#!pip install gtfs_functions

In [39]:
#conda install geopandas

In [4]:
import numpy as np
import pandas as pd
import math
import matplotlib.pyplot as plt
import seaborn as sns
import networkx as nx
import random
from geopy import distance
from tqdm.notebook import tqdm
tqdm.pandas()
import time
from numpy.random import multinomial
from operator import itemgetter
from datetime import datetime, timedelta
import pickle
import gtfs_functions as gtfs

In [5]:
orari_metro = pd.read_csv('data/tpl_metroorari.csv', sep = ';')
percorsi_metro = pd.read_csv('data/tpl_metropercorsi.csv', sep = ';')
orari_sup = pd.read_csv('data/tpl_orari.csv', sep = ';')
percorsi_sup = pd.read_csv('data/tpl_percorsi.csv', sep = ';')
fermate_metro = pd.read_csv('data/tpl_metrofermate.csv', sep = ';')
fermate_sup = pd.read_csv('data/tpl_fermate.csv', sep = ';')
sequenza_metro = pd.read_csv('data/tpl_metrosequenza.csv', sep = ';')
sequenza_sup = pd.read_csv('data/tpl_sequenza.csv', sep = ';')
keep = pd.read_csv('data/keep.csv', index_col=0)
am_counts_df = pd.read_csv('data/nodes_attr_cat.csv')
routes, stops, stop_times, trips, shapes = gtfs.import_gtfs("data/AMAT_gtfs.zip")

### Displaying Source Data

Below we display the source data we are starting from.

In [6]:
percorsi_sup.head()

linea mezzo  percorso verso                                      nome  \
0      1  TRAM     12560    Di                           Roserio - Greco   
1      1  TRAM      9457    As                           Greco - Roserio   
2     10  TRAM     10930    As  Lunigiana - 24 Maggio (LAV. MONUMENTALE)   
3     10  TRAM     10933    Di  24 Maggio - Lunigiana (LAV. MONUMENTALE)   
4    115   BUS     10025    As                   Gratosoglio - P.za Diaz   

  tipo_perc  lung_km  num_ferm  LONG_X_4326_CENTROID  LAT_Y_4326_CENTROID  \
0  Canonico    13.82        48              9.169741            45.485975   
1  Canonico    13.97        47              9.169414            45.486312   
2  Canonico    10.12        35              9.178067            45.475305   
3  Canonico     9.99        35              9.178169            45.474864   
4  Canonico     7.35        21              9.179332            45.433933   

                               Location  
0  (45.4859750999615, 9.16974100864072)  
1  (45.4863116993006, 9.16941433348211)  
2  (45.4753045559618, 9.17806739004007)  
3   (45.4748642272165, 9.1781685490565)  
4   (45.4339331905209, 9.1793322250523)

In [7]:
display_side_by_side(fermate_sup.head(),sequenza_sup.head())

id_amat 
 ubicazione 
 linee 
 LONG_X_4326 
 LAT_Y_4326 
 Location 
 
 
 
 
 0 
 10001 
 Via Matteotti, 19 prima di Via Cavour 
 89 
 9.140993 
 45.531514 
 (45.5315142888777, 9.1409928380588) 
 
 
 1 
 10002 
 Via Cavour, 32/e dopo Via Morandi (ACI) 
 89 
 9.144455 
 45.532308 
 (45.5323077151981, 9.14445524902009) 
 
 
 2 
 10003 
 Via Bovisasca, 18 dopo Via C.Battisti 
 89 
 9.148258 
 45.526906 
 (45.5269056419672, 9.14825811356353) 
 
 
 3 
 10008 
 Via Bovisasca, 15/A prima di Via Baracca 
 89 
 9.148455 
 45.526752 
 (45.5267523716675, 9.14845459686126) 
 
 
 4 
 10009 
 Via Rimembranze prima di Via Cornicione 
 89 
 9.143783 
 45.530035 
 (45.5300346693961, 9.14378251859864) 
 
 
 
 
 
 
 percorso 
 num 
 id_ferm 
 
 
 
 
 0 
 10151 
 7 
 13331 
 
 
 1 
 6774 
 16 
 11915 
 
 
 2 
 12162 
 26 
 10635 
 
 
 3 
 322 
 11 
 13691 
 
 
 4 
 12273 
 2 
 13284

In [12]:
orari_sup.head()

linea mezzo  percorso        orario tipo_giorno inizio   fine  corse_gior  \
0     48   BUS      8989  INV2021-2022           L  07:05  21:35          29   
1     39   BUS     11333  INV2021-2022           F  06:25  21:57          49   
2     80   BUS      8119  INV2021-2022           F  01:25  05:15           8   
3    925   BUS      7691  INV2021-2022           F  07:40  19:49          15   
4    115   BUS     10025  INV2021-2022           S  01:28  05:51           9   

   corse_punt  corse_morb  corse_sera  
0           4           4           0  
1           5           5           0  
2           0           0           0  
3           2           3           0  
4           0           0           0

In [11]:
stop_times.head(1)

trip_id  arrival_time  departure_time stop_id  \
0  20210904_f5i_10549_36825678       20747.0         20747.0   14883   

   stop_sequence stop_headsign  pickup_type drop_off_type  \
0             18           NaN          0.0             0   

   shape_dist_traveled route_id  ... stop_code          stop_name stop_desc  \
0                  NaN     B220  ...       NaN  Via Matteotti, 35       NaN   

  zone_id stop_url location_type parent_station stop_timezone  \
0     NaN      NaN           NaN            NaN           NaN   

   wheelchair_boarding                  geometry  
0                  NaN  POINT (9.14579 45.37565)  

[1 rows x 23 columns]

# 2. DataFrame Manipulation<a name="df"></a>

<div class="alert alert-success" >
In this section we manipulate the source data to extract the information we need to build our network.

In [18]:
# Put together timetables of surface vehicles and metro
orari = pd.concat([orari_sup, orari_metro]).reset_index(drop = True)
orari['next_day'] = orari.inizio > orari.fine

# only keep timetables for week days
percorsi_L_metro = orari[(orari.tipo_giorno == 'L') & (orari.mezzo == 'METRO')].percorso.unique()
percorsi_L_sup = orari[(orari.tipo_giorno == 'L') & (orari.mezzo != 'METRO')&(orari.linea != 151)].percorso.unique()

In [19]:
# Creating a dictionary of routes edges per route
percorsi = dict()
for i in percorsi_L_sup:
    linea = percorsi_sup[percorsi_sup.percorso == i].mezzo.values[0] + str(percorsi_sup[percorsi_sup.percorso == i].linea.values[0])
    m = sequenza_sup[sequenza_sup.percorso == i].sort_values('num').id_ferm.values
    e = [(m[i], m[i+1], linea) for i in range(len(m) -1)]
    percorsi[i] = e

for i in percorsi_L_metro:
    linea = percorsi_metro[percorsi_metro.percorso == i].mezzo.values[0] + str(percorsi_metro[percorsi_metro.percorso == i].linea.values[0])
    m = sequenza_metro[sequenza_metro.percorso == i].sort_values('num').id_ferm.values
    e = [(m[i], m[i+1], linea) for i in range(len(m) -1)]
    percorsi[i] = e

In [20]:
# put together underground and surface transit stops
fermate = pd.concat([fermate_metro[['id_amat', 'nome']], 
            fermate_sup[['id_amat', 'ubicazione']].rename(columns={'ubicazione':'nome'})])

In [8]:
orari.head()

linea mezzo  percorso        orario tipo_giorno inizio   fine  corse_gior  \
0     48   BUS      8989  INV2021-2022           L  07:05  21:35          29   
1     39   BUS     11333  INV2021-2022           F  06:25  21:57          49   
2     80   BUS      8119  INV2021-2022           F  01:25  05:15           8   
3    925   BUS      7691  INV2021-2022           F  07:40  19:49          15   
4    115   BUS     10025  INV2021-2022           S  01:28  05:51           9   

   corse_punt  corse_morb  corse_sera  next_day  
0           4           4           0     False  
1           5           5           0     False  
2           0           0           0     False  
3           2           3           0     False  
4           0           0           0     False

In [21]:
# transform time into minutes from midnight
orari.inizio = orari['inizio'].apply(lambda x: datetime.strptime(x, '%H:%M').time().hour*60 + datetime.strptime(x, '%H:%M').time().minute)
orari.fine = orari['fine'].apply(lambda x: datetime.strptime(x, '%H:%M').time().hour*60 + datetime.strptime(x, '%H:%M').time().minute)

# 3. Creating the Network<a name="net"></a>

<div class="alert alert-success" >
In this section we create the base network of our model. Each node represents a stop and each edge represents a path between two stops. It is a multigraph since two stops can be connected by multiple vehicles and it is directed since each edge represents a one-way link.
    
Edges have the following attributes: 
    
- weight (distance/speed of the transport mode)
- transport mode
- total capacity, which depends on the transport mode
- next edge(s) in the route
- transport line
- color, which depends on the transport mode
- passengers list
- waiting list.
    
Nodes have one attribute for each category of amenities and the values is the number of facilities of that category that can be reached from the stop.

In [13]:
def makeMultiGraph(df, speeds, coords, capacity):
    '''
    Generating a multi directed graph with the information regarding the speeds and the capacities of the transport means and 
    the geographic coordinates of the stops.
    '''

    G = nx.MultiDiGraph()

    edges = []
    edges += [(i,j,l, {'weight':distance.distance(coords[i], coords[j]).km/speeds[b],'trans_mode':b, 'color':a, 
                       'lines':l, 'waiting_list':[], 'passengers_list':[], 'total_capacity':capacity[b]}) 
                for i,j,a,b,l in df.loc[:,['f_from','f_to', 'color', 'trans_mode', 'lines']].values]


    G.add_edges_from(edges)
  
    return G

In [14]:
def plot_graph(G, coords, figsize = (20,20), dpi = 500):
    '''
    Plot the network.
    '''
    plt.figure(figsize=figsize, dpi=dpi)
    color_comp = nx.get_edge_attributes(G,'color').values()
    nx.draw_networkx(G, pos = coords, with_labels=False, node_size=1,edge_color=color_comp, arrowsize = 4, label = colors)
    plt.legend()

In [15]:
def next_edge(G, edge):
    '''
    For each edge identifies the following edge on the path of the respective line.
    '''
    return G[edge[0]][edge[1]][edge[2]]['next_edges']

In [22]:
# assign a color to each vehicle for plotting purposes
colors = {1: 'red', 2: 'green', 3: 'yellow', 4: 'blue', 5: 'violet', 'TRAM': 'brown', 'BUS': 'pink', 'FILOBUS': 'grey'}

# assign speeds to each vehicle based on their commercial speeds
speeds = {1: 32, 2: 32, 3: 32, 4: 32, 5: 32, 'TRAM': 11, 'BUS': 14, 'FILOBUS': 14, 'foot': 5}

# assign capacity assuming total number of passengers = 1'500'000 changing on average 8 vehicles per day
# and a simulated population of 20'000 agents
ratio = 10 # each agent represents 10 travelers
capacity = {1: 1230//ratio, 2: 1230//ratio, 3: 1230//ratio, 4: 1230//ratio, 5: 1230//ratio, 
            'TRAM': 215//ratio, 'BUS': 100//ratio, 'FILOBUS': 130//ratio, 'foot': np.inf}

edge = pd.DataFrame(columns=['f_from', 'f_to', 'color'])
coords = dict()

# build dataframe with edges and their attributes
for i in percorsi_L_metro:
    color = percorsi_metro[percorsi_metro.percorso == i].linea.values[0]
    linea = percorsi_metro[percorsi_metro.percorso == i].mezzo.values[0] + str(percorsi_metro[percorsi_metro.percorso == i].linea.values[0])
    m = sequenza_metro[sequenza_metro.percorso == i].sort_values('num')
    n_stops = max(m.num)
    m['ferm'] = m.id_ferm.shift(-1)
    edges = m[['id_ferm', 'ferm']][:-1].astype(int).rename(columns={'id_ferm':'f_from', 'ferm':'f_to'}).reset_index(drop=True)
    edges['color'] = [colors[color] for i in range(n_stops-1)]
    edges['lines'] = [linea for i in range(n_stops-1)]
    edges['trans_mode'] = [color for i in range(n_stops-1)]
    edge = pd.concat([edge, edges])
    df1 = pd.merge(m[['id_ferm']], fermate_metro[['id_amat', 'LONG_X_4326', 'LAT_Y_4326']], left_on= 'id_ferm', right_on='id_amat')

    coord = {df1.id_ferm[i]: (df1.LONG_X_4326[i], df1.LAT_Y_4326[i]) for i in range(n_stops)}
    coords = {**coords, **coord}

for i in percorsi_L_sup:
    color = percorsi_sup[percorsi_sup.percorso == i].mezzo.values[0]
    linea = percorsi_sup[percorsi_sup.percorso == i].mezzo.values[0] + str(percorsi_sup[percorsi_sup.percorso == i].linea.values[0])
    m = sequenza_sup[sequenza_sup.percorso == i].sort_values('num')
    n_stops = max(m.num)
    m['ferm'] = m.id_ferm.shift(-1)
    edges = m[['id_ferm', 'ferm']][:-1].astype(int).rename(columns={'id_ferm':'f_from', 'ferm':'f_to'}).reset_index(drop=True)
    edges['color'] = [colors[color] for i in range(n_stops-1)]
    edges['lines'] = [linea for i in range(n_stops-1)]
    edges['trans_mode'] = [color for i in range(n_stops-1)]
    edge = pd.concat([edge, edges])
    df1 = pd.merge(m[['id_ferm']], fermate_sup[['id_amat', 'LONG_X_4326', 'LAT_Y_4326']], left_on= 'id_ferm', right_on='id_amat')
    coord = {df1.id_ferm[i]: (df1.LONG_X_4326[i], df1.LAT_Y_4326[i]) for i in range(n_stops)}
    coords = {**coords, **coord}


In [25]:
edges.head()

f_from   f_to color   lines trans_mode
0   16547  16548  pink  BUS566        BUS
1   16548  16549  pink  BUS566        BUS
2   16549  16550  pink  BUS566        BUS
3   16550  16551  pink  BUS566        BUS
4   16551  16552  pink  BUS566        BUS

In [15]:
# graph without foot edges
G_multi = makeMultiGraph(edge, speeds, coords, capacity)

In [16]:
fermate_before = fermate.id_amat.unique() # all stops 
fermate_after = np.array(G_multi.nodes()) # stops in our network

In [17]:
# # plot graph without foot edges
#plot_graph(G_multi, coords, figsize = (20,20), dpi = 500)

In [18]:
# adding foot edges to connect stops that are closer than 200m
foot_edges = keep[(keep['0'].isin(fermate_after)) & (keep['1'].isin(fermate_after))]

G_multi2 = G_multi.copy()
foot = []
for i, j in foot_edges.values:
    if (i,j) not in G_multi2.edges():
        G_multi2.add_edge(i, j, key = 'foot', weight = distance.distance(coords[i], coords[j]).km/speeds['foot'], 
                        color = 'lightskyblue', trans_mode = 'foot', lines = 'foot', waiting_list=[], 
                        passengers_list=[], total_capacity=capacity['foot'])
        foot.append((i,j,'foot'))
    if (j, i) not in G_multi2.edges():
        G_multi2.add_edge(j, i, key = 'foot', weight = distance.distance(coords[i], coords[j]).km/speeds['foot'],  
                        color = 'lightskyblue', trans_mode = 'foot', lines = 'foot', waiting_list=[], 
                        passengers_list=[], total_capacity=capacity['foot'])
        foot.append((j, i,'foot'))

In [19]:
# checking the difference with before-foot-edges graph (in terms of number of edges)
len(G_multi.edges()), len(G_multi2.edges())

(6713, 18470)

In [18]:
# plot complete graph
plot_graph(G_multi2, coords)

In [20]:
# attributing the number of amenities to nodes
am_counts = am_counts_df.set_index('Unnamed: 0').T.to_dict()
nx.set_node_attributes(G_multi2, am_counts)

In [21]:
# extracting only stops present in fermate_after, i.e., the final network
am_counts_df = am_counts_df.rename(columns = {"Unnamed: 0":"stops_id"}).set_index('stops_id')
am_counts_df = am_counts_df.loc[fermate_after]
am_counts_df.head()

leisure  food  school  office
stops_id                               
934            12     2       0       4
901             2     2       0       0
989            26    14       0       4
896             5     3       0       1
945             1     3       0       0

In [21]:
#am_counts_df.to_csv("data/am_counts_df.csv")

In [22]:
#finding next edges of the same line for each edge in the network
next_edges = dict()
for e in G_multi2.edges:
    if e[2] != 'foot':
        n = e[1]
        l = []
        for i in list(G_multi2.out_edges(n, data = True)):
            if i[2]['lines'] == e[2] and i[1] != e[0]:
                l.append((i[0], i[1], i[2]['lines']))
        next_edges[e] = l
    else:
        next_edges[e] = []

In [23]:
# attributing next edges to edges
for i in G_multi2.edges:
    G_multi2[i[0]][i[1]][i[2]]['next_edges'] = next_edges[i]

In [25]:
# G_multi2 = nx.read_gpickle("data/G.gpickle")

# 4. Getting Routes Timetables<a name="route"></a>

<div class="alert alert-success" >
In this section we extract the activation time for each edge (i.e., the time at which each vehicle passes by a stop). The output is a dictionary containing a set of times for each edge.

GTFS Download: https://transitfeeds.com/p/agenzia-mobilita-ambiente-territorio/341 , https://www.agenziatpl.it/open-data/gtfs

In [29]:
stop_times.head(1)

trip_id  arrival_time  departure_time stop_id  \
0  20210904_f5i_10549_36825678       20747.0         20747.0   14883   

   stop_sequence stop_headsign  pickup_type drop_off_type  \
0             18           NaN          0.0             0   

   shape_dist_traveled route_id  ... stop_code          stop_name stop_desc  \
0                  NaN     B220  ...       NaN  Via Matteotti, 35       NaN   

  zone_id stop_url location_type parent_station stop_timezone  \
0     NaN      NaN           NaN            NaN           NaN   

   wheelchair_boarding                  geometry  
0                  NaN  POINT (9.14579 45.37565)  

[1 rows x 23 columns]

In [25]:
# select only non empty columns
stops_time = stop_times[["route_id","direction_id","stop_sequence","stop_id","stop_name","arrival_time",
                         "departure_time","trip_id", "geometry"]]

stops_time = stops_time.sort_values(["route_id", "direction_id", "stop_sequence", "arrival_time"]).reset_index(drop = True)

# transform time in correct format and keep only arrival time
stops_time["arrival_time_adj"] = stops_time.arrival_time.apply(lambda x: time.strftime('%H:%M:%S', time.gmtime(x)))
stops_time["departure_time_adj"] = stops_time.departure_time.apply(lambda x: time.strftime('%H:%M:%S', time.gmtime(x)))
stops_time = stops_time[["route_id", "direction_id", "stop_sequence", "stop_id", "stop_name", "arrival_time_adj", "trip_id", "geometry"]]
stops_time = stops_time.rename(columns = {"arrival_time_adj": "arrival_time"})
stops_time.head()

route_id  direction_id  stop_sequence stop_id             stop_name  \
0     B121           0.0              1   14204  p.le stz s.donato m3   
1     B121           0.0              1   14204  p.le stz s.donato m3   
2     B121           0.0              1   14204  p.le stz s.donato m3   
3     B121           0.0              1   14204  p.le stz s.donato m3   
4     B121           0.0              1   14204  p.le stz s.donato m3   

  arrival_time                                       trip_id  \
0     05:05:00  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265165   
1     05:35:00  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265193   
2     05:45:00  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265167   
3     05:50:00  20210904_2_MARTEDI_INV_SUB_f5i_4873_26265237   
4     05:55:00  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265185   

                   geometry  
0  POINT (9.25605 45.42897)  
1  POINT (9.25605 45.42897)  
2  POINT (9.25605 45.42897)  
3  POINT (9.25605 45.42897)  
4  POINT (9.25605 45.42897)

In [27]:
print("Unique stops in stops_info:",stops_time.stop_id.nunique())
print("Unique lines in stops_info:", stops_time.route_id.nunique())

Unique stops in stops_info: 4908
Unique lines in stops_info: 155


Creating a dataframe with edges information.

In [28]:
edges = G_multi2.edges(data = True)

In [29]:
# exclude foot edges
sup_edges = []
for i in edges:
    if i[2]["trans_mode"] != "foot":
        sup_edges.append(i)

In [30]:
# create df
edges_df = pd.DataFrame(sup_edges)

In [31]:
def extract(row, key):
    """
    Extracting info from Attributes column.
    """
    if key == "weight":
        weight = row[2]["weight"]
        return weight
    if key == "trans_mode":
        trans_mode = row[2]["trans_mode"]
        return trans_mode
    if key == "lines":
        lines= row[2]["lines"]
        return lines 

# fill df with edges attributes
edges_df["weight"] = edges_df.apply(lambda x: extract(x, "weight"), axis = 1)
edges_df["trans_mode"] = edges_df.apply(lambda x: extract(x, "trans_mode"), axis = 1)
edges_df["lines"] = edges_df.apply(lambda x: extract(x, "lines"), axis = 1)
edges_df = edges_df.drop(columns = 2)
edges_df = edges_df.rename(columns = {0: "start_stop", 1: "end_stop"})

In [32]:
def line_extr(row, what):
    """
    Extracting the number of the line or the transit mean.
    """
    line = row["lines"]
    try:
        num = int(line[-3:])
        if what == "num":
            return num
        elif what == "transit":
            return line[:-3]
    except: 
        try:
            num = int(line[-2:])
            if what == "num":
                return num
            elif what == "transit":
                return line[:-2]
        except:
            num = int(line[-1])
            if what == "num": 
                return num
            elif what == "transit":
                return line[:-1]
            
# add additional info to the df
edges_df["line_num"] = edges_df.apply(lambda x: line_extr(x, "num"), axis = 1)
edges_df["line_trans"] = edges_df.apply(lambda x: line_extr(x, "transit"), axis = 1)

In [33]:
edges_df.head()

start_stop  end_stop    weight trans_mode   lines  line_num line_trans
0         934       901  0.013893        1.0  METRO1         1      METRO
1         934       927  0.011795        1.0  METRO1         1      METRO
2         901       989  0.014156        1.0  METRO1         1      METRO
3         901       934  0.013893        1.0  METRO1         1      METRO
4         989       896  0.016072        1.0  METRO1         1      METRO

In [34]:
#edges_df.to_csv("data/edges_updated.csv", index = False)

Creating dictionary with edges' activation time.

In [35]:
def extr_min(row):
    """
    Convert arrival time from string to time and map it to count of minutes from midnight.
    """
    time = row["arrival_time"]
    time = datetime.strptime(time, "%H:%M:%S").time()
    minutes = time.hour*60 + time.minute
    
    return minutes

# add the converted time to the df
stops_time["arrival_time"] = stops_time.apply(lambda x: extr_min(x), axis = 1)

In [36]:
def correct_metro_nodes(row, fermate):
    """
    Mapping Metro stops IDs to integers.
    """
    id_ = row["stop_id"]
    try:
        id_ = int(id_)
        return id_
    except:
        id_ = fermate[fermate["nome"]== id_].id_amat.tolist()[0]
        return id_

# correct the format of stop_id
stops_time["stop_id"] = stops_time.apply(lambda x:correct_metro_nodes(x, fermate), axis = 1)

In [37]:
# mapping some GTFS routes to their equivalent on the routes provided by Comune di Milano
stand_route_d = {"T179":"BUS179",
                 "BN25":"BUS125",
                 "BN26":"BUS126",
                 "BNM1":"BUS151",
                 "BNM2":"BUS152",
                 "BNM3":"BUS153"}

In [38]:
def stand_route(row, stand_route_d):
    """
    Standardizing the route id.
    """
    route = row["route_id"]
    
    try:
        return stand_route_d[route]
    except:  
        try:
            num = int(route[-3:])
            type_ = route[:-3]
        except: 
            try:
                num = int(route[-2:])
                type_ = route[:-2]
            except:
                num = int(route[-1])
                type_ = route[:-1]
            
    if type_ == "T":
        type_ = "TRAM"
    elif type_ == "M":
        type_ = "METRO"
    elif type_[0] == "B":
        type_ = "BUS"
    
    return f"{type_}{num}"

# change route_id so that it matches data from AMAT
stops_time["route_id"] = stops_time.apply(lambda x: stand_route(x, stand_route_d), axis = 1)

In [39]:
stops_time = stops_time.rename(columns = {"route_id": "lines"}) # for homogeneity

In [40]:
# apply the line_extr function to stops_time df as well
stops_time["line_num"] = stops_time.apply(lambda x: line_extr(x, "num"), axis = 1)
stops_time["line_trans"] = stops_time.apply(lambda x: line_extr(x, "transit"), axis = 1)

In [41]:
stops_time.head()

lines  direction_id  stop_sequence  stop_id             stop_name  \
0  BUS121           0.0              1    14204  p.le stz s.donato m3   
1  BUS121           0.0              1    14204  p.le stz s.donato m3   
2  BUS121           0.0              1    14204  p.le stz s.donato m3   
3  BUS121           0.0              1    14204  p.le stz s.donato m3   
4  BUS121           0.0              1    14204  p.le stz s.donato m3   

   arrival_time                                       trip_id  \
0           305  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265165   
1           335  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265193   
2           345  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265167   
3           350  20210904_2_MARTEDI_INV_SUB_f5i_4873_26265237   
4           355  20210904_2_MARTEDI_INV_SUB_f5i_4872_26265185   

                   geometry  line_num line_trans  
0  POINT (9.25605 45.42897)       121        BUS  
1  POINT (9.25605 45.42897)       121        BUS  
2  POINT (9.25605 45.42897)       121        BUS  
3  POINT (9.25605 45.42897)       121        BUS  
4  POINT (9.25605 45.42897)       121        BUS

In [42]:
def filobus(row):
    """
    Momentarily converting Filobus to Bus in edges_df since they are not distinguished in the GTFS files 
    (i.e. in stops_time).
    """
    transit = row["line_trans"]
    if transit == "FILOBUS":
        return "BUS"
    else:
        return transit
    
# momentarily converting Filobus to Bus in the df
edges_df["line_trans"] = edges_df.apply(lambda x: filobus(x), axis = 1)

In [31]:
def active_time(row, stops_time):
    """
    Finding edges' activation times.
    """
    start = row["start_stop"]
    end = row["end_stop"]
    edge_type = row["lines"]
    edge_line_trans = row["line_trans"]
    edge_line_num = row["line_num"]
    
    # df with all times the means of transit of the node passes by this stop
    # need to specify the direction too (i.e. the following node/stop of the edge)
    df = stops_time[(stops_time["stop_id"]== start)&(stops_time["line_num"]== edge_line_num)
                    &(stops_time["line_trans"]== edge_line_trans)]
    
    stop_seq = df["stop_sequence"].unique() # probably 2 values: passing through that same stop once per "direction"
    times = set() #  where to store the times
    
    for i in stop_seq:
        # df with info for the next stop (i+1) of that same line, to find the trip_id / direction (if it exists)
        df_next = stops_time[(stops_time["stop_sequence"]== i+1)&(stops_time["line_num"]==edge_line_num)
                             &(stops_time["line_trans"]== edge_line_trans)&(stops_time["stop_id"]== end)]
        
        trip_id = df_next["trip_id"].unique().tolist() # find the IDs of the trip
        if trip_id: # if there is indeed at least a trip going from i to i+1. It would be more efficient to check
                    # for the direction instead, however there are multiple NaN entries
            for j in trip_id:
                times.update(df[df["trip_id"] == j].arrival_time.tolist())
    return times

<div class="alert alert-danger" >
Takes 1h to run!

In [44]:
# # updating the dataframe
# edges_df["times"] = edges_df.progress_apply(lambda x: active_time(x, stops_time), axis = 1);
# edges_df.to_csv("data/edges_with_minutes_updated.csv", index = False)

  0%|          | 0/6713 [00:00<?, ?it/s]

In [45]:
edges_df = pd.read_csv("data/edges_with_minutes_updated.csv")
edges_df.head()

start_stop  end_stop    weight trans_mode   lines  line_num line_trans  \
0         934       901  0.013893        1.0  METRO1         1      METRO   
1         934       927  0.011795        1.0  METRO1         1      METRO   
2         901       989  0.014156        1.0  METRO1         1      METRO   
3         901       934  0.013893        1.0  METRO1         1      METRO   
4         989       896  0.016072        1.0  METRO1         1      METRO   

                                               times  
0  {1024, 0, 514, 1029, 519, 1034, 524, 1038, 15,...  
1  {1024, 0, 514, 1029, 519, 1031, 1034, 523, 524...  
2  {1, 1026, 516, 1031, 521, 1035, 525, 1040, 16,...  
3  {1, 13, 16, 31, 51, 354, 363, 371, 377, 382, 3...  
4  {513, 1027, 3, 517, 1032, 522, 1037, 527, 1041...

In [46]:
# will have to reconvert some BUS to FILOBUS
edges_old = pd.read_csv("data/edges_updated.csv")
edges_old[edges_old["line_trans"]== "FILOBUS"].lines.unique()

array(['FILOBUS90', 'FILOBUS92', 'FILOBUS93', 'FILOBUS91'], dtype=object)

In [47]:
def gen_edge_act_dict(row, d):
    """
    Generating a dictionary having edges as keys and all the times it activates as value.
    """
    start = row["start_stop"]
    end = row["end_stop"]
    line = row["lines"]
    times = row["times"]
    
    if line in ["BUS90", "BUS91", "BUS92", "BUS93"]:
        line = "FILOBUS" + line[3:]
        
    key = (start, end, line)
    d[key] = times
    
    return d

d_active_edges = {}
edges_df.apply(lambda x: gen_edge_act_dict(x, d_active_edges), axis = 1 )

# fixing an edge
update_edge = [746, 772, 797, 825, 854, 884, 913, 943, 975, 1000, 1024, 1047, 1069, 1092, 1116, 1137, 
               1161, 1182, 1205]
    
d_active_edges[(13335, 13324, 'BUS73')].update(update_edge)

# adding foot edges
active_foot = [i for i in range(1440)]

for e in tqdm(foot):

    d_active_edges[e] = active_foot

  0%|          | 0/11757 [00:00<?, ?it/s]

In [48]:
# example
d_active_edges[(934, 901, 'METRO1')]

{0,
 15,
 340,
 344,
 353,
 361,
 369,
 376,
 384,
 391,
 397,
 400,
 405,
 408,
 413,
 419,
 425,
 430,
 435,
 440,
 444,
 449,
 454,
 458,
 463,
 468,
 472,
 477,
 482,
 486,
 491,
 496,
 500,
 505,
 510,
 514,
 519,
 524,
 528,
 533,
 537,
 542,
 547,
 552,
 557,
 563,
 567,
 572,
 579,
 587,
 594,
 601,
 609,
 616,
 624,
 631,
 639,
 646,
 654,
 661,
 669,
 676,
 684,
 691,
 699,
 706,
 714,
 721,
 729,
 736,
 744,
 751,
 759,
 766,
 774,
 781,
 789,
 796,
 802,
 809,
 816,
 822,
 829,
 836,
 842,
 849,
 856,
 862,
 869,
 876,
 882,
 889,
 896,
 902,
 909,
 916,
 922,
 929,
 936,
 942,
 949,
 956,
 962,
 969,
 976,
 983,
 989,
 995,
 1001,
 1007,
 1013,
 1019,
 1024,
 1029,
 1034,
 1038,
 1043,
 1048,
 1053,
 1057,
 1062,
 1067,
 1072,
 1076,
 1081,
 1085,
 1090,
 1094,
 1099,
 1103,
 1108,
 1112,
 1117,
 1121,
 1126,
 1130,
 1135,
 1140,
 1145,
 1149,
 1154,
 1159,
 1163,
 1169,
 1176,
 1182,
 1189,
 1197,
 1205,
 1213,
 1223,
 1233,
 1242,
 1251,
 1262,
 1272,
 1282,
 1293,
 1305

In [49]:
# get a set of all buses and exclude foot and 151
all_buses = set()
for edge in d_active_edges.keys():
    all_buses.add(edge[2])
all_buses = list(all_buses.difference({'foot','BUS151'}))

In [50]:
# adjusting timetables for our one-minute timestep
for bus in tqdm(all_buses):
    edges = []
    
    # get all means of transport
    for k, v in d_active_edges.items():
        if k[2] == bus:
            edges.append(k)
    c = True
    while c:
        c = False # check is false
        for i, e in enumerate(edges[::-1]):
            next_e = next_edge(G_multi2, e)
            
            if len(next_e) > 0:
                next_e = next_e[0]
                orari_e = d_active_edges[e] # timetable of the edge
                orari_nexte = d_active_edges[next_e] # timetable of the next edge
                orari_uguali = orari_e.intersection(orari_nexte)
                
                if len(orari_uguali) > 0: # if the vehicle is at two different stops at the same minute
                    orari_shifted = [x+1 for x in orari_uguali] # shifts timetable by one minute
                    orari_nuovi = (orari_nexte - orari_uguali).union(orari_shifted) 
                    d_active_edges[next_e] = orari_nuovi # update timetable
                    c = True # check becomes true so that we have to loop again
                    
                if i == len(edges): # specific case for the last edge
                    orari_e = d_active_edges[e]
                    orari_nexte = d_active_edges[next_e]
                    orari_uguali = orari_e.intersection(orari_nexte)
                    
                    if len(orari_uguali) > 0:
                        c = True
                        orari_shifted = [x+1 for x in orari_uguali]
                        orari_nuovi = (orari_nexte - orari_uguali).union(orari_shifted)
                        d_active_edges[next_e] = orari_nuovi

  0%|          | 0/136 [00:00<?, ?it/s]

# 5. Saving Files<a name="save"></a>

In [72]:
# # saving d_active_edges
# outfile = open("data/d_active_edges",'wb')
# pickle.dump(d_active_edges, outfile)
# outfile.close()

In [56]:
# # saving foot list
# outfile = open("data/foot.pkl",'wb')
# pickle.dump(foot, outfile)
# outfile.close()

In [26]:
# # saving network
#nx.write_gpickle(G_multi2, "data/G.gpickle")

In [81]:
# # saving coordinates 
# outfile = open("data/coords.pkl",'wb')
# pickle.dump(coords, outfile)
# outfile.close()

In [27]:
# # saving fermate df
#fermate.to_csv("data/fermate.csv", index = False)

In [34]:
# # saving percorsi 
# outfile = open("data/percorsi",'wb')
# pickle.dump(percorsi, outfile)
# outfile.close()

In [35]:
# # saving orari
# orari.to_csv("data/orari.csv", index = False)